In [415]:
import numpy as np
import pandas as pd
#import stata file using pandas
raw_data = pd.read_stata('./HCMST_2017_public_data_v1.1_stata/HCMST_2017_draft_v1.1.dta')
#import data schema
data_schema = pd.read_csv('./cleaned_HCMST_2017_schema.csv', header=0, index_col=0)
#uses variables labels in data schema to create a survey glossary of terms
data_glossary = data_schema['variable_label']

In [416]:
print(data_glossary.loc['ppincimp'])
raw_data.shape

Household Income 


(3510, 285)

In [417]:
raw_data['w6_q12']

0                  Leans Republican
1                  Leans Republican
2                    Leans Democrat
3       Undecided/Independent/Other
4                   Strong Democrat
5       Undecided/Independent/Other
6                  Leans Republican
7                    Leans Democrat
8                               NaN
9                    Leans Democrat
10                   Leans Democrat
11      Undecided/Independent/Other
12                  Strong Democrat
13                   Leans Democrat
14              Not Strong Democrat
15                  Strong Democrat
16      Undecided/Independent/Other
17                  Strong Democrat
18                 Leans Republican
19                  Strong Democrat
20      Undecided/Independent/Other
21                  Strong Democrat
22              Not Strong Democrat
23                   Leans Democrat
24      Undecided/Independent/Other
25      Undecided/Independent/Other
26                 Leans Republican
27                 Leans Rep

## Analysis Goals

The following are the questions we are trying to answer with the data set:

1) Where are the top fives places couples met that resulted in the marriages that lasted the longest?

2) Does the difference in income between partners affect the length of marriage?

3) Does religiosity affect the length of marriage?

4) Does political leanings affect the length of marriage?

5) Does ethnicity affect the length of marriage?

6) Does the age at which couples met affect the length of marriage?

**During Data Cleaning, we should only collect features which help us answer these questions**


In [418]:
#show all rows, set max column width to 1000px to see the full text
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', 1000)
data_schema = data_schema.reset_index()
data_schema

variable_name storage_type  \
0                                                        CaseID          int   
1                                                    CASEID_NEW         long   
2                                                         qflag         byte   
3                                                       weight1       double   
4                                                weight1_freqwt        float   
5                                                       weight2       double   
6                                                      weight1a       double   
7                                               weight1a_freqwt        float   
8                                                  weight_combo        float   
9                                           weight_combo_freqwt        float   
10                                                     duration          int   
11                                                   speed_flag         byte   
12                                                      consent         byte   
13                                                         xlgb         byte   
14                                                           S1         byte   
15                                                           S2         byte   
16                                                           S3         byte   
17                                                   DOV_Branch         byte   
18                                                   Q3_Refused         byte   
19                                                           Q4         byte   
20                                                           Q5         byte   
21                                                          Q6A         byte   
22                                                          Q6B         byte   
23                                                           Q9         byte   
24                                                          Q10         byte   
25                                                          Q11         byte   
26                                                          Q12         byte   
27                                                          Q14         byte   
28                                                        Q15A7         byte   
29                                                          Q16         byte   
30                                                  Q16_Refused         byte   
31                                                         Q17A         byte   
32                                                         Q17B         byte   
33                                                         Q17C         byte   
34                                                         Q17D         byte   
35                                                          Q19         byte   
36                                                          Q20         byte   
37                                                    Q21A_Year         byte   
38                                                   Q21A_Month         byte   
39                                                    Q21B_Year         byte   
40                                                   Q21B_Month         byte   
41                                                    Q21C_Year         byte   
42                                                   Q21C_Month         byte   
43                                                    Q21D_Year         byte   
44                                                   Q21D_Month         byte   
45                                                  w6_identity         byte   
46                                                   w6_outness         byte   
47                                            w6_outness_timing         byte   
48                                                          Q23         byte   
49                                                

In [419]:
#choose categories to keep
cat_to_keep = ['S1', 'Q21A_Year', 'Q21D_2_Year',
               'ppp20072', 'interracial_5cat', 'ppage', 
               'w6_q9', 'ppeducat', 'w6_q10', 'ppgender', 'ppincimp', 'ppethm', 'w6_q6b', 'partyid7', 'w6_q12']
cat_new_labels = ['Married', 'FirstMet_Year', 'Married_Year',
                  'Religious_Attendance', 'Interracial_Couple', 'Age', 'P_Age',
                 'Education', 'P_Education', 'Gender', 'Household_Income', 'Ethnicity', 'P_Ethnicity', 'Politics', 'P_Politics']

In [420]:
#use for loop to collect more categories
for i in range(152,167):
    cat_to_keep.append(data_schema['variable_name'].iloc[i])
    cat_new_labels.append(data_schema['variable_label'].iloc[i])

In [421]:
#use for loop to collect more categories
for i in range(251,272):
    cat_to_keep.append(data_schema['variable_name'].iloc[i])
    cat = data_schema['variable_name'].iloc[i]
    cat_new_labels.append(cat[cat.find('_', len(data_schema['variable_name'].iloc[i])//2)+1:])

In [422]:
#clean cat labels
for c in range(len(cat_new_labels)):
    if 'Q14: ' in cat_new_labels[c]:
        cat_new_labels[c] = cat_new_labels[c].replace('Q14: ', '')

In [423]:
#new data set
data_set = raw_data[cat_to_keep].copy()
data_set.columns = cat_new_labels 

In [424]:
data_set

Married FirstMet_Year Married_Year   Religious_Attendance  \
0     No, I am not Married           NaN          NaN                  Never   
1        Yes, I am Married          1983          NaN                  Never   
2        Yes, I am Married          2006          NaN  Once or twice a month   
3     No, I am not Married           NaN          NaN                  Never   
4        Yes, I am Married          1983          NaN    Once a year or less   
5        Yes, I am Married          1981          NaN            Once a week   
6        Yes, I am Married          1966          NaN            Once a week   
7        Yes, I am Married          1967          NaN                  Never   
8     No, I am not Married           NaN          NaN                    NaN   
9     No, I am not Married           NaN          NaN  More than once a week   
10       Yes, I am Married          2008          NaN                  Never   
11    No, I am not Married           NaN          NaN                  Never   
12    No, I am not Married           NaN          NaN                  Never   
13    No, I am not Married           NaN          NaN    Once a year or less   
14       Yes, I am Married          2007          NaN                  Never   
15       Yes, I am Married          2002          NaN    Once a year or less   
16    No, I am not Married          2007          NaN     A few times a year   
17       Yes, I am Married          2002          NaN                  Never   
18       Yes, I am Married          2004          NaN     A few times a year   
19       Yes, I am Married          1973          NaN            Once a week   
20       Yes, I am Married          1995          NaN    Once a year or less   
21    No, I am not Married           NaN          NaN                  Never   
22    No, I am not Married           NaN         2015                  Never   
23    No, I am not Married          2008          NaN                  Never   
24       Yes, I am Married          2000          NaN                  Never   
25       Yes, I am Married          1990          NaN  More than once a week   
26    No, I am not Married           NaN          NaN     A few times a year   
27    No, I am not Married          2014          NaN    Once a year or less   
28    No, I am not Married          2012          NaN  More than once a week   
29    No, I am not Married          2010          NaN     A few times a year   
30       Yes, I am Married          2006          NaN                  Never   
31    No, I am not Married           NaN         1989                  Never   
32       Yes, I am Married          1977          NaN    Once a year or less   
33    No, I am not Married           NaN          NaN     A few times a year   
34       Yes, I am Married       Refused          NaN  More than once a week   
35       Yes, I am Married          1999          NaN            Once a week   
36    No, I am not Married          2016          NaN            Once a week   
37       Yes, I am Married          1999          NaN     A few times a year   
38    No, I am not Married          2010          NaN                  Never   
39    No, I am not Married           NaN          NaN                    NaN   
40       Yes, I am Married          1988          NaN    Once a year or less   
41    No, I am not Married          2013          NaN                  Never   
42       Yes, I am Married          2006          NaN                  Never   
43    No, I am not Married          2017          NaN                  Never   
44    No, I am not Married          2015          NaN    Once a year or less   
45       Yes, I am Married          2000          NaN                  Never   
46       Yes, I am Married          2015          NaN  Once or twice a month   
47       Yes, I am Married          1971          NaN                  Never   
48       Yes, I am Married          2015          NaN  Once or twice a month   
49    No, I am not 

In [425]:
data_set.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3510 entries, 0 to 3509
Data columns (total 51 columns):
 #   Column                             Non-Null Count  Dtype   
---  ------                             --------------  -----   
 0   Married                            3510 non-null   category
 1   FirstMet_Year                      2856 non-null   category
 2   Married_Year                       132 non-null    category
 3   Religious_Attendance               3394 non-null   category
 4   Interracial_Couple                 3365 non-null   category
 5   Age                                3510 non-null   category
 6   P_Age                              3374 non-null   float64 
 7   Education                          3510 non-null   category
 8   P_Education                        3394 non-null   category
 9   Gender                             3510 non-null   category
 10  Household_Income                   3510 non-null   category
 11  Ethnicity                          3510 non

In [426]:
data_set

Married FirstMet_Year Married_Year   Religious_Attendance  \
0     No, I am not Married           NaN          NaN                  Never   
1        Yes, I am Married          1983          NaN                  Never   
2        Yes, I am Married          2006          NaN  Once or twice a month   
3     No, I am not Married           NaN          NaN                  Never   
4        Yes, I am Married          1983          NaN    Once a year or less   
5        Yes, I am Married          1981          NaN            Once a week   
6        Yes, I am Married          1966          NaN            Once a week   
7        Yes, I am Married          1967          NaN                  Never   
8     No, I am not Married           NaN          NaN                    NaN   
9     No, I am not Married           NaN          NaN  More than once a week   
10       Yes, I am Married          2008          NaN                  Never   
11    No, I am not Married           NaN          NaN                  Never   
12    No, I am not Married           NaN          NaN                  Never   
13    No, I am not Married           NaN          NaN    Once a year or less   
14       Yes, I am Married          2007          NaN                  Never   
15       Yes, I am Married          2002          NaN    Once a year or less   
16    No, I am not Married          2007          NaN     A few times a year   
17       Yes, I am Married          2002          NaN                  Never   
18       Yes, I am Married          2004          NaN     A few times a year   
19       Yes, I am Married          1973          NaN            Once a week   
20       Yes, I am Married          1995          NaN    Once a year or less   
21    No, I am not Married           NaN          NaN                  Never   
22    No, I am not Married           NaN         2015                  Never   
23    No, I am not Married          2008          NaN                  Never   
24       Yes, I am Married          2000          NaN                  Never   
25       Yes, I am Married          1990          NaN  More than once a week   
26    No, I am not Married           NaN          NaN     A few times a year   
27    No, I am not Married          2014          NaN    Once a year or less   
28    No, I am not Married          2012          NaN  More than once a week   
29    No, I am not Married          2010          NaN     A few times a year   
30       Yes, I am Married          2006          NaN                  Never   
31    No, I am not Married           NaN         1989                  Never   
32       Yes, I am Married          1977          NaN    Once a year or less   
33    No, I am not Married           NaN          NaN     A few times a year   
34       Yes, I am Married       Refused          NaN  More than once a week   
35       Yes, I am Married          1999          NaN            Once a week   
36    No, I am not Married          2016          NaN            Once a week   
37       Yes, I am Married          1999          NaN     A few times a year   
38    No, I am not Married          2010          NaN                  Never   
39    No, I am not Married           NaN          NaN                    NaN   
40       Yes, I am Married          1988          NaN    Once a year or less   
41    No, I am not Married          2013          NaN                  Never   
42       Yes, I am Married          2006          NaN                  Never   
43    No, I am not Married          2017          NaN                  Never   
44    No, I am not Married          2015          NaN    Once a year or less   
45       Yes, I am Married          2000          NaN                  Never   
46       Yes, I am Married          2015          NaN  Once or twice a month   
47       Yes, I am Married          1971          NaN                  Never   
48       Yes, I am Married          2015          NaN  Once or twice a month   
49    No, I am not 

In [427]:
data_set[['FirstMet_Year','Married_Year']][data_set['Married_Year'].notna()]

FirstMet_Year Married_Year
22             NaN         2015
31             NaN         1989
62             NaN         1972
86             NaN         1965
122            NaN         1992
148            NaN         1968
153            NaN         1981
178            NaN         1988
188            NaN         1992
254            NaN         1991
275            NaN         1982
283            NaN         2005
289            NaN         2011
290            NaN         1990
345            NaN         1990
366            NaN         1959
373            NaN         1961
437            NaN         1963
481            NaN         1974
493            NaN         1978
515            NaN         1995
523            NaN         1975
537            NaN         2013
543            NaN         1978
568            NaN      Refused
577            NaN         1964
620            NaN         1977
627            NaN         1959
640            NaN         1984
667            NaN         1987
675            NaN         1998
712            NaN         1981
747            NaN         1983
765            NaN         1986
770            NaN         1948
779            NaN         1961
800            NaN         1985
841            NaN         1968
859            NaN         1978
865            NaN         1987
904            NaN         1964
947            NaN      Refused
949            NaN         1963
966            NaN         1948
967            NaN      Refused
997            NaN         1976
1021           NaN         1978
1045           NaN         1969
1049           NaN         1992
1052           NaN         2012
1053           NaN         1997
1094           NaN         2010
1119           NaN         2000
1143           NaN         1950
1156           NaN         1972
1168           NaN         1970
1169           NaN         1985
1178           NaN         1987
1179           NaN         1960
1181           NaN      Refused
1272           NaN         1997
1347           NaN         2013
1369           NaN         2000
1434           NaN         2001
1489           NaN         1981
1500           NaN         1961
1528           NaN         1985
1558           NaN         2004
1582           NaN         1972
1667           NaN         1965
1677           NaN         1962
1702           NaN         2003
1706           NaN         2002
1724           NaN         2015
1754           NaN         1977
1763           NaN         1975
1800           NaN         1999
1823           NaN         1985
1845           NaN         1989
1858           NaN         2007
1865           NaN         1952
1878           NaN      Refused
1897           NaN         1964
1913           NaN         2012
1925           NaN         1962
1973           NaN         1983
1983           NaN         1991
2063           NaN         1979
2236           NaN         1989
2252           NaN         2010
2274           NaN         1992
2307           NaN         1991
2366           NaN         1978
2367           NaN         1999
2380           NaN         2007
2434           NaN         2009
2452           NaN         1973
2486           NaN         1998
2499           NaN         1970
2509           NaN         1967
2530           NaN      Refused
2532           NaN         1983
2541           NaN         1976
2690           NaN         1979
2695           NaN         2008
2705           NaN         2017
2734           NaN         1977
2790           NaN         1972
2816           NaN         1966
2830           NaN         1980
2846           NaN         1963
2877           NaN         1981
2912           NaN         1995
2941           NaN         2002
3021           NaN         1980
3022           NaN      Refused
3030           NaN         1993
3045           NaN         1976
3086           NaN         1970
3111           NaN         1985
3162           NaN         1990
3176           NaN         2000
3189           NaN         1970
3204           NaN         1972
3225 

In [428]:
#Married couples do not report the first year at which they met. Let's combine them as 'First_Together'
data_set.insert(loc=1,column='First_Together',value=pd.Series(data_set['FirstMet_Year'].copy()))
for i in range(data_set['FirstMet_Year'].shape[0]):
    if data_set['FirstMet_Year'].iloc[i] is np.nan:
        data_set['First_Together'].iloc[i] = data_set['Married_Year'].iloc[i]

In [429]:
#check to see if 'First_Together' has successfully incorporated 'Married_Year' values
data_set[['First_Together','Married_Year']][data_set['Married_Year'].notna()]

First_Together Married_Year
22             2015         2015
31             1989         1989
62             1972         1972
86             1965         1965
122            1992         1992
148            1968         1968
153            1981         1981
178            1988         1988
188            1992         1992
254            1991         1991
275            1982         1982
283            2005         2005
289            2011         2011
290            1990         1990
345            1990         1990
366            1959         1959
373            1961         1961
437            1963         1963
481            1974         1974
493            1978         1978
515            1995         1995
523            1975         1975
537            2013         2013
543            1978         1978
568         Refused      Refused
577            1964         1964
620            1977         1977
627            1959         1959
640            1984         1984
667            1987         1987
675            1998         1998
712            1981         1981
747            1983         1983
765            1986         1986
770            1948         1948
779            1961         1961
800            1985         1985
841            1968         1968
859            1978         1978
865            1987         1987
904            1964         1964
947         Refused      Refused
949            1963         1963
966            1948         1948
967         Refused      Refused
997            1976         1976
1021           1978         1978
1045           1969         1969
1049           1992         1992
1052           2012         2012
1053           1997         1997
1094           2010         2010
1119           2000         2000
1143           1950         1950
1156           1972         1972
1168           1970         1970
1169           1985         1985
1178           1987         1987
1179           1960         1960
1181        Refused      Refused
1272           1997         1997
1347           2013         2013
1369           2000         2000
1434           2001         2001
1489           1981         1981
1500           1961         1961
1528           1985         1985
1558           2004         2004
1582           1972         1972
1667           1965         1965
1677           1962         1962
1702           2003         2003
1706           2002         2002
1724           2015         2015
1754           1977         1977
1763           1975         1975
1800           1999         1999
1823           1985         1985
1845           1989         1989
1858           2007         2007
1865           1952         1952
1878        Refused      Refused
1897           1964         1964
1913           2012         2012
1925           1962         1962
1973           1983         1983
1983           1991         1991
2063           1979         1979
2236           1989         1989
2252           2010         2010
2274           1992         1992
2307           1991         1991
2366           1978         1978
2367           1999         1999
2380           2007         2007
2434           2009         2009
2452           1973         1973
2486           1998         1998
2499           1970         1970
2509           1967         1967
2530        Refused      Refused
2532           1983         1983
2541           1976         1976
2690           1979         1979
2695           2008         2008
2705           2017         2017
2734           1977         1977
2790           1972         1972
2816           1966         1966
2830           1980         1980
2846           1963         1963
2877           1981         1981
2912           1995         1995
2941           2002         2002
3021           1980         1980
3022        Refused      Refused
3030           1993         1993
3045           1976         1976
3086           1970         1970
3111           1985         1985
3162        

In [430]:
#Once the two columns are combined as 'First_Together', drop original columns, convert "Refused" to np.nan
#Filter data set such that we only preserve entries where 'First_Together' is not np.nan
data_set.drop(columns=['FirstMet_Year', 'Married_Year'],inplace=True)
data_set['First_Together'].replace({'Refused': np.nan}, inplace=True)
data_set = data_set[data_set['First_Together'].notna()]

In [431]:
data_set['P_Age'].unique()

array([52., 45., 59., 60., 67., 65., 43., 35., 42., 37., 40., 72., 25.,
       55., 22., 26., 63., 75., 32., 24., 62., 53., 58., 28., 48., 34.,
       64., 23., 54., 36., 70., 29., 41., 74., 56., 21., 38., 57., 30.,
       71., 73., 49., 50., 68., 61., 46., 69., 27., 80., 47., 39., 76.,
       77., 66., 51., 83., 44., 95., -1., nan, 31., 85., 78., 20., 33.,
       79., 81., 87., 86., 84., 18., 82., 89., 19., 90., 17., 91., 10.,
       14., 16., 94.])

In [432]:
#convert numeric categories to numeric type
data_set[['First_Together','Age', 'P_Age']] = data_set.loc[:,['First_Together', 'Age', 'P_Age']].apply(lambda x: pd.to_numeric(x))
#drop row where P_Age is NaN, inf or negative
data_set = data_set[data_set['P_Age'] > 0]

c:\users\grant\documents\learningstuff\datascienceprojects\date_marriage_hcmst_2017\venv\lib\site-packages\pandas\core\frame.py:2963: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [433]:
data_set.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2928 entries, 1 to 3509
Data columns (total 50 columns):
 #   Column                             Non-Null Count  Dtype   
---  ------                             --------------  -----   
 0   Married                            2928 non-null   category
 1   First_Together                     2928 non-null   int64   
 2   Religious_Attendance               2928 non-null   category
 3   Interracial_Couple                 2906 non-null   category
 4   Age                                2928 non-null   int64   
 5   P_Age                              2928 non-null   float64 
 6   Education                          2928 non-null   category
 7   P_Education                        2928 non-null   category
 8   Gender                             2928 non-null   category
 9   Household_Income                   2928 non-null   category
 10  Ethnicity                          2928 non-null   category
 11  P_Ethnicity                        2928 non

In [434]:
data_set['P_Age'] = data_set.loc[:,['P_Age']].apply(lambda x: x.astype('int64'))

In [435]:
data_set.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2928 entries, 1 to 3509
Data columns (total 50 columns):
 #   Column                             Non-Null Count  Dtype   
---  ------                             --------------  -----   
 0   Married                            2928 non-null   category
 1   First_Together                     2928 non-null   int64   
 2   Religious_Attendance               2928 non-null   category
 3   Interracial_Couple                 2906 non-null   category
 4   Age                                2928 non-null   int64   
 5   P_Age                              2928 non-null   int64   
 6   Education                          2928 non-null   category
 7   P_Education                        2928 non-null   category
 8   Gender                             2928 non-null   category
 9   Household_Income                   2928 non-null   category
 10  Ethnicity                          2928 non-null   category
 11  P_Ethnicity                        2928 non

In [436]:
#create a column to figure out years together. Survey is taken in 2017
new_col = data_set.loc[:,['First_Together']].apply(lambda x: 2017 - x)
data_set.insert(loc=1, column='Years_Together', value=pd.Series(new_col.First_Together))

In [437]:
#create a column to figure out age difference between partners
new_col = abs(data_set['Age'] - data_set['P_Age'])
data_set.insert(loc=5, column='Age_Diff', value=list(new_col))

In [438]:
#export cleaned dataset as cleaned_data.csv
data_set.to_csv('clean_data.csv', index=False)